* **Goal of the day:** Show how to do a spring network dynamics
* **Coder:** Paul Valcke

In [3]:
import sys
sys.path.insert(0,  "../../" )
import chimes as chm
import numpy as np 
import matplotlib.pyplot as plt

import plotly.graph_objects as go
import numpy as np

In [ ]:
def plot_spring_network(hub,Node1,Node2,L0,returnFig=False):

    Nspring=len(Node1)

    R=hub.get_dfields()
    nt = R['nt']['value']
    x = R[  'x']['value'][:,0,0,:,0]
    y = R[  'y']['value'][:,0,0,:,0]
    fx = R['Fx']['value'][:,0,0,:,0]
    fy = R['Fy']['value'][:,0,0,:,0]
    FMX = R['Fmx']['value'][:,0,0,:,:]
    FMY = R['Fmy']['value'][:,0,0,:,:]
    m = R['m']['value'][0,0,:,0]

    Springreldist = np.zeros((nt,Nspring))
    for k in range(Nspring):
        Springreldist[:,k]= ((x[:,Node1[k]]-x[:,Node2[k]])**2 + 
                            (y[:,Node1[k]]-y[:,Node2[k]])**2)**(1/2) 
        Springreldist[:,k] /= L0[k]


    # Function to create quiver plot
    def create_quiver(x, y, u, v, scale=0.2, color='black'):
        quivers = []
        for xi, yi, ui, vi in zip(x, y, u, v):
            quivers.append(go.Scatter(
                x=[xi, xi + ui*scale],
                y=[yi, yi + vi*scale],
                mode='lines',
                line=dict(color=color),
                showlegend=False
            ))
            # Add larger arrow head
            quivers.append(go.Scatter(
                x=[xi + ui*scale],
                y=[yi + vi*scale],
                mode='markers',
                marker=dict(size=10, color=color, symbol='star-triangle-up'),
                showlegend=False
            ))
        return quivers

    # Function to get color based on Springreldist value
    def get_color(value):
        value = 0.5*(1+np.tanh(100*(value-1)))
        #value = max(0, min(value, 3))  # Clamp the value between 0 and 3
        red = int(255 * value)
        blue = 255 - red
        return f'rgb({red}, 0, {blue})'
    def scatt(x,y,t,m):
        return go.Scatter(
        x=x[t],
        y=y[t],
        mode='markers',
        marker=dict(size=10*m**(1/3), color='black'),
        name='Nodes'
    )
    def springline(x,y,Node1,Node2,Springreldist,t):
        color = get_color(Springreldist[0, i])
        return go.Scatter(
                x=[x[t, Node1[i]], x[t, Node2[i]]],
                y=[y[t, Node1[i]], y[t, Node2[i]]],
                mode='lines',
                line=dict(width=2, color=color),
                showlegend=False
            )
    # Create initial scatter plot and quiver plot
    fig = go.Figure()


    fig.add_trace(scatt(x,y,0,m=10))                    # Add scatter plot for nodes
    quivers = create_quiver(x[0], y[0], fx[0], fy[0])   # Add quiver plot for forces
    for q in quivers: fig.add_trace(q)
    for i in range(Nspring): fig.add_trace(springline(x,y,Node1,Node2,Springreldist,0))

    # Create frames for animation
    frames = []
    for t in range(nt):
        frame_data = [scatt(x,y,t,m)]
        quivers = create_quiver(x[t], y[t], fx[t], fy[t])
        frame_data.extend(quivers)
        for i in range(Nspring): frame_data.append(springline(x,y,Node1,Node2,Springreldist,t))
        frames.append(go.Frame(data=frame_data, name=str(t)))


    # Update layout with fixed axis limits
    fig.update_layout(
        xaxis=dict(range=[np.min(x)-1, np.max(x)+1], scaleanchor="y", scaleratio=1),
        yaxis=dict(range=[np.min(y)-1, np.max(y)+1]),
        updatemenus=[{
            'buttons': [
                {
                    'args': [None, {'frame': {'duration': 50, 'redraw': True}, 'fromcurrent': True}],
                    'label': 'Play',
                    'method': 'animate'
                },
                {
                    'args': [[None], {'frame': {'duration': 0, 'redraw': True}, 'mode': 'immediate', 'transition': {'duration': 0}}],
                    'label': 'Pause',
                    'method': 'animate'
                }
            ],
            'direction': 'left',
            'pad': {'r': 10, 't': 87},
            'showactive': False,
            'type': 'buttons',
            'x': 0.1,
            'xanchor': 'right',
            'y': 0,
            'yanchor': 'top'
        }],
        sliders=[{
            'steps': [{'args': [[f.name], {'frame': {'duration': 50, 'redraw': True}, 'mode': 'immediate', 'transition': {'duration': 0}}],
                    'label': str(k),
                    'method': 'animate'} for k, f in enumerate(frames)],
            'active': 0,
            'transition': {'duration': 0},
            'x': 0.1,
            'xanchor': 'left',
            'y': 0,
            'yanchor': 'top'
        }]
    )

    fig.frames = frames

    if returnFig:
        return fig 
    else:
        fig.show()


In [1]:
import numpy as np

# Given Inputs
N = 5  # Number of masses
M = 3  # Number of springs

# Nodes 
m  = np.array([1, 2, 1.5, 2.5, 1.8], dtype=float)
x  = np.array([0, 1, 2, 1, 0], dtype=float)
y  = np.array([0, 0, 1, 2, 1], dtype=float)
vx = np.array([0, 0, 0, 0, 0], dtype=float)
vy = np.array([0, 0, 0, 0, 0], dtype=float)


k  = np.array([10, 15, 20], dtype=float) # Spring constants (example values)
L0 = np.array([ 1,  1, 1], dtype=float)  # Rest lengths of the springs (example values)
Node1 = np.array([0, 1, 2], dtype=int)   # Indices of masses connected by each spring (example values)
Node2 = np.array([1, 2, 3], dtype=int)


# Function to compute the stiffness matrices for x and y components
def compute_stiffness_matrices(N, M, k, L0, Node1, Node2, x, y):
    Kx = np.zeros((N, N), dtype=float)
    Ky = np.zeros((N, N), dtype=float)
    for i in range(M):
        n1 = int(Node1[i])
        n2 = int(Node2[i])
        k_val = k[i]
        L0_val = L0[i]
        
        dx = x[n2] - x[n1]
        dy = y[n2] - y[n1]
        L = np.sqrt(dx**2 + dy**2)
        
        if L == 0:
            continue
        
        c = dx / L
        s = dy / L
        k_local = k_val * (1 - L0_val / L)
        
        Kx_local = k_local * np.array([[c*c, -c*c],
                                       [-c*c, c*c]], dtype=float)
        
        Ky_local = k_local * np.array([[s*s, -s*s],
                                       [-s*s, s*s]], dtype=float)
        
        Kx[n1, n1] += Kx_local[0, 0]
        Kx[n1, n2] += Kx_local[0, 1]
        Kx[n2, n1] += Kx_local[1, 0]
        Kx[n2, n2] += Kx_local[1, 1]
        
        Ky[n1, n1] += Ky_local[0, 0]
        Ky[n1, n2] += Ky_local[0, 1]
        Ky[n2, n1] += Ky_local[1, 0]
        Ky[n2, n2] += Ky_local[1, 1]
    
    return Kx, Ky

# Compute the stiffness matrices for x and y components
Kx, Ky = compute_stiffness_matrices(N, M, k, L0, Node1, Node2, x, y)

# Initial displacements and velocities
ux = x.copy().astype(float)
uy = y.copy().astype(float)
vx = vx.copy().astype(float)
vy = vy.copy().astype(float)

# External forces (example values)
Fx = np.zeros(N, dtype=float)
Fy = np.zeros(N, dtype=float)

# Time step and duration for simulation
dt = 0.1
time = 100
steps = int(time / dt)

# Arrays to store trajectories and forces over time
trajectory_x = np.zeros((steps, N))
trajectory_y = np.zeros((steps, N))
force_x = np.zeros((steps, N))
force_y = np.zeros((steps, N))

# Simulation
for step in range(steps):
    ax = Fx - np.dot(Kx, ux) / m
    ay = Fy - np.dot(Ky, uy) / m
    
    vx += ax * dt
    vy += ay * dt
    
    ux += vx * dt
    uy += vy * dt
    
    # Store trajectories and forces
    trajectory_x[step, :] = ux
    trajectory_y[step, :] = uy
    force_x[step, :] = Fx
    force_y[step, :] = Fy

In [4]:
Nspring=M
nt = steps
x = trajectory_x
y = trajectory_y
fx = force_x
fy = force_y
#FMX = R['Fmx']['value'][:,0,0,:,:]
#FMY = R['Fmy']['value'][:,0,0,:,:]
m = m

Springreldist = np.zeros((nt,Nspring))
for k in range(Nspring):
    Springreldist[:,k]= ((x[:,Node1[k]]-x[:,Node2[k]])**2 + 
                        (y[:,Node1[k]]-y[:,Node2[k]])**2)**(1/2) 
    Springreldist[:,k] /= L0[k]


# Function to create quiver plot
def create_quiver(x, y, u, v, scale=0.2, color='black'):
    quivers = []
    for xi, yi, ui, vi in zip(x, y, u, v):
        quivers.append(go.Scatter(
            x=[xi, xi + ui*scale],
            y=[yi, yi + vi*scale],
            mode='lines',
            line=dict(color=color),
            showlegend=False
        ))
        # Add larger arrow head
        quivers.append(go.Scatter(
            x=[xi + ui*scale],
            y=[yi + vi*scale],
            mode='markers',
            marker=dict(size=10, color=color, symbol='star-triangle-up'),
            showlegend=False
        ))
    return quivers

# Function to get color based on Springreldist value
def get_color(value):
    value = 0.5*(1+np.tanh(100*(value-1)))
    #value = max(0, min(value, 3))  # Clamp the value between 0 and 3
    red = int(255 * value)
    blue = 255 - red
    return f'rgb({red}, 0, {blue})'
def scatt(x,y,t,m):
    return go.Scatter(
    x=x[t],
    y=y[t],
    mode='markers',
    marker=dict(size=10*m**(1/3), color='black'),
    name='Nodes'
)
def springline(x,y,Node1,Node2,Springreldist,t):
    color = get_color(Springreldist[0, i])
    return go.Scatter(
            x=[x[t, Node1[i]], x[t, Node2[i]]],
            y=[y[t, Node1[i]], y[t, Node2[i]]],
            mode='lines',
            line=dict(width=2, color=color),
            showlegend=False
        )
# Create initial scatter plot and quiver plot
fig = go.Figure()


fig.add_trace(scatt(x,y,0,m=10))                    # Add scatter plot for nodes
quivers = create_quiver(x[0], y[0], fx[0], fy[0])   # Add quiver plot for forces
for q in quivers: fig.add_trace(q)
for i in range(Nspring): fig.add_trace(springline(x,y,Node1,Node2,Springreldist,0))

# Create frames for animation
frames = []
for t in range(nt):
    frame_data = [scatt(x,y,t,m)]
    quivers = create_quiver(x[t], y[t], fx[t], fy[t])
    frame_data.extend(quivers)
    for i in range(Nspring): frame_data.append(springline(x,y,Node1,Node2,Springreldist,t))
    frames.append(go.Frame(data=frame_data, name=str(t)))


# Update layout with fixed axis limits
fig.update_layout(
    xaxis=dict(range=[np.min(x)-1, np.max(x)+1], scaleanchor="y", scaleratio=1),
    yaxis=dict(range=[np.min(y)-1, np.max(y)+1]),
    updatemenus=[{
        'buttons': [
            {
                'args': [None, {'frame': {'duration': 50, 'redraw': True}, 'fromcurrent': True}],
                'label': 'Play',
                'method': 'animate'
            },
            {
                'args': [[None], {'frame': {'duration': 0, 'redraw': True}, 'mode': 'immediate', 'transition': {'duration': 0}}],
                'label': 'Pause',
                'method': 'animate'
            }
        ],
        'direction': 'left',
        'pad': {'r': 10, 't': 87},
        'showactive': False,
        'type': 'buttons',
        'x': 0.1,
        'xanchor': 'right',
        'y': 0,
        'yanchor': 'top'
    }],
    sliders=[{
        'steps': [{'args': [[f.name], {'frame': {'duration': 50, 'redraw': True}, 'mode': 'immediate', 'transition': {'duration': 0}}],
                'label': str(k),
                'method': 'animate'} for k, f in enumerate(frames)],
        'active': 0,
        'transition': {'duration': 0},
        'x': 0.1,
        'xanchor': 'left',
        'y': 0,
        'yanchor': 'top'
    }]
)

fig.frames = frames


fig.show()


In [11]:
N=np.zeros((10,10))
A = np.random.randint(10,size=100)
B = np.random.randint(10,size=100)

In [12]:
print(A)
print(B)

[8 8 4 6 0 7 5 5 8 4 4 5 7 8 6 2 8 7 4 3 0 2 6 3 8 9 8 4 8 3 9 1 5 1 2 3 4
 4 7 7 1 5 3 1 6 5 9 7 5 2 2 0 9 9 8 3 0 3 9 1 2 4 2 7 2 4 1 8 4 1 3 3 7 8
 7 1 6 1 8 9 5 1 5 4 5 6 1 7 2 1 1 7 8 1 8 8 3 7 2 1]
[2 1 1 7 4 5 0 6 5 1 4 0 9 2 4 4 2 1 2 6 1 6 2 8 6 1 5 2 2 3 9 8 6 6 7 4 3
 5 6 9 1 9 6 6 0 3 1 9 6 5 8 5 4 0 6 9 5 2 5 3 7 9 6 3 2 8 3 6 7 4 7 2 0 1
 2 5 1 2 5 1 8 3 4 3 2 2 0 9 2 5 9 7 3 6 6 5 3 1 1 8]


In [13]:
N[A,B]+=1

In [14]:
N

array([[0., 1., 0., 0., 1., 1., 0., 0., 0., 0.],
       [1., 1., 1., 1., 1., 1., 1., 0., 1., 1.],
       [0., 1., 1., 0., 1., 1., 1., 1., 1., 0.],
       [0., 0., 1., 1., 1., 0., 1., 1., 1., 1.],
       [0., 1., 1., 1., 1., 1., 0., 1., 1., 1.],
       [1., 0., 1., 1., 1., 0., 1., 0., 1., 1.],
       [1., 1., 1., 0., 1., 0., 0., 1., 0., 0.],
       [1., 1., 1., 1., 0., 1., 1., 1., 0., 1.],
       [0., 1., 1., 1., 0., 1., 1., 0., 0., 0.],
       [1., 1., 0., 0., 1., 1., 0., 0., 0., 1.]])